In [1]:
from datasets import load_dataset

dataset = load_dataset('taln-ls2n/kptimes')

No config specified, defaulting to: kp_times/raw


Extracting data files:   0%|          | 0/3 [00:00<?, ?it/s]

Generating train split: 0 examples [00:00, ? examples/s]

Generating test split: 0 examples [00:00, ? examples/s]

Generating validation split: 0 examples [00:00, ? examples/s]

Dataset kp_times downloaded and prepared to /Users/boudin-f/.cache/huggingface/datasets/taln-ls2n___kp_times/raw/1.1.0/81f75cd972e595c55ef8cc865e898b0bc01ce7d220287a246b566b7417f07274. Subsequent calls will reuse this data.


  0%|          | 0/3 [00:00<?, ?it/s]

In [3]:
from tqdm.notebook import tqdm

P, R, M, U, nb_kps = [], [], [], [], []

for split in ['train', 'validation', 'test']:
    
    for sample in tqdm(dataset[split]):
        nb_kps.append(len(sample["keyphrases"]))
        P.append(sample["prmu"].count("P") / nb_kps[-1])
        R.append(sample["prmu"].count("R") / nb_kps[-1])
        M.append(sample["prmu"].count("M") / nb_kps[-1])
        U.append(sample["prmu"].count("U") / nb_kps[-1])
        
print("# keyphrases: {:.2f}".format(sum(nb_kps)/len(nb_kps)))
print("% P: {:.2f}".format(sum(P)/len(P)*100))
print("% R: {:.2f}".format(sum(R)/len(R)*100))
print("% M: {:.2f}".format(sum(M)/len(M)*100))
print("% U: {:.2f}".format(sum(U)/len(U)*100))

  0%|          | 0/259923 [00:00<?, ?it/s]

  0%|          | 0/10000 [00:00<?, ?it/s]

  0%|          | 0/20000 [00:00<?, ?it/s]

# keyphrases: 5.03
% P: 46.64
% R: 15.11
% M: 28.89
% U: 9.36


In [4]:
import spacy

nlp = spacy.load("en_core_web_sm")

# https://spacy.io/usage/linguistic-features#native-tokenizer-additions

from spacy.lang.char_classes import ALPHA, ALPHA_LOWER, ALPHA_UPPER
from spacy.lang.char_classes import CONCAT_QUOTES, LIST_ELLIPSES, LIST_ICONS
from spacy.util import compile_infix_regex

# Modify tokenizer infix patterns
infixes = (
    LIST_ELLIPSES
    + LIST_ICONS
    + [
        r"(?<=[0-9])[+\-\*^](?=[0-9-])",
        r"(?<=[{al}{q}])\.(?=[{au}{q}])".format(
            al=ALPHA_LOWER, au=ALPHA_UPPER, q=CONCAT_QUOTES
        ),
        r"(?<=[{a}]),(?=[{a}])".format(a=ALPHA),
        # ✅ Commented out regex that splits on hyphens between letters:
        # r"(?<=[{a}])(?:{h})(?=[{a}])".format(a=ALPHA, h=HYPHENS),
        r"(?<=[{a}0-9])[:<>=/](?=[{a}])".format(a=ALPHA),
    ]
)

infix_re = compile_infix_regex(infixes)
nlp.tokenizer.infix_finditer = infix_re.finditer

In [ ]:
doc_len = []
for split in ['train', 'validation', 'test']:
    for sample in tqdm(dataset[split]):
        doc_len.append(len(nlp(sample["title"])) + len(nlp(sample["abstract"])))
print("avg doc len: {:.1f}".format(sum(doc_len)/len(doc_len)))

  0%|          | 0/259923 [00:00<?, ?it/s]